## PTAL（墨田区）　データ作成手順書

#### 文責：氏川智皓
##### (2025年4月作成)
- Graduate Student, Luskin School of Public Affairs, University of California, Los Angeles
- 千葉大学予防医学センター　プロジェクト研究員

---

#### プロジェクトの概要
「Transit Desert（交通空白地帯）」という用語は、公共交通の需要と供給の間に大きなギャップが存在する地域を指します。こうした交通空白地帯の問題に対応するには、公共交通へのアクセス状況を評価し、交通インフラの整備に優先順位をつけることが重要です。

イギリスやインドでは、公共交通へのアクセスを評価する手法として PTAL（Public Transport Accessibility Level） というツールが使われています。東京は高度に発達した公共交通網を持つ都市として知られていますが、交通需要と供給のミスマッチは依然として存在しています。現在のところ、日本ではPTALが公共交通の評価ツールとして活用されていません。

本プロジェクトでは、東京都墨田区における公共交通アクセスをPTALを用いて評価することを目的としています。このプロジェクトで作成されるPTALデータは、他のデータセットと組み合わせて活用され、墨田区における公共交通アクセスの不平等を是正するための根拠資料としての役割が期待されます。

---

#### 使用データ

1. 100mメッシュのポリゴンデータ  
   [（国土数値情報 -> 土地利用細分メッシュ（地域5339、世界測地系、2021年度](https://nlftp.mlit.go.jp/ksj/gml/datalist/KsjTmplt-L03-b-2021.html#!)
2. バス停の位置情報  
   [（国土数値情報 -> バス停留所データ -> 東京都 -> 2022年度）](https://nlftp.mlit.go.jp/ksj/gml/datalist/KsjTmplt-P11-2022.html)
3. 駅の位置情報  
   [（国土数値情報 -> 鉄道データ -> 2023年度）](https://nlftp.mlit.go.jp/ksj/gml/datalist/KsjTmplt-N02-2023.html)
4. 2020年国勢調査の境界線データ（小地域（町丁・字等））  
   [境界データ -> 小地域 -> 国勢調査2020 -> 小地域（町丁・字等）（JGD2000） -> 世界測地系緯度経度・Shapefile -> 東京都 -> 墨田区](https://www.e-stat.go.jp/gis/statmap-search?page=1&type=2&aggregateUnitForBoundary=A&toukeiCode=00200521&toukeiYear=2020&serveyId=A002005212020&prefCode=13&coordsys=1&format=shape&datum=2000)
5. 各SAP（駅・バス停）における、各路線の運行頻度に関する情報（時刻表）（インターネット上）

---

#### Step 0-1: SAPs (Service Access Points）とメッシュの中心点とを結ぶデータの作成（ArcGIS Proを使用）

* 上記1-4のデータのArcGISへのインポート 
* 町丁のポリゴンデータを市区町村名でフィルタリングして、墨田区のポリゴンだけを選択 → dissolveして墨田区の区界ポリゴンを作成（`Sumida_Border.geojson`）
* メッシュデータと墨田区の区界ポリゴンを使って、墨田区に含まれるメッシュを抽出（select by location → export）（intersect：境界線と一部でも交差するものは含める）（`Sumida_mesh.geojson`）
* 各メッシュの重心点のポイントデータを作成（feature to point）→ indexの値をコピーして`MeshID`という列を作る）（`Sumida_mesh_centroids.geojson`）
* 墨田区の区界の1km外側のポリゴンを作成（バッファーポリゴン）（SAPになりうるのは最も遠い点でも墨田区の区界から960m以内。不要なSAPを含めるとOD Cost Analysisで不必要なcredit消費をしてしまうため）
* バス停・駅のデータとバッファーポリゴンを使って、バッファー内に含まれるバス停・駅のポイントだけを抽出（select by location）（+indexの値をコピーしてそれぞれに`BusStopID`、`StationID`という列を作る） 
* 駅はlineなのでfeature to pointでpointデータに変換 
* 墨田区内のメッシュの重心点とバッファー内のバス停・駅のポイントデータを使って、**Make OD Cost Matrix Layer**というtoolを使って、各重心点と徒歩距離で640m圏内にあるバス停と960m圏内にある駅をそれぞれ抽出し（4.8km/hでそれぞれ8分、12分）、それぞれの組み合わせにおける徒歩距離を算出（`mesh_to_busstops.geojason`と`mesh_to_stations.geojson`としてエクスポート）
* `mesh_to_busstops.geojason`とバッファー内のバス停リストとをinner joinすることでMake OD Cost Matrix Layerに使用された`BusStopID`を抽出（駅も同様）（`Sumida_BusStops_Point.geojson`と`Sumida_Stations_Point.geojson`）


注：メッシュデータ、バス停や駅のデータを作った時に、`MeshID`と`StationID`, `BusStopID`という列を用意しておく事を忘れずに（インデックスとは別で用意しておく）  
注：メッシュやバス停・駅の数が多く一括処理できない場合は、メッシュを分割して処理 

#### Step 0-2: 各SAPにおける運行頻度データの作成（インターネット上からexcelに手入力）

* バッファー内に含まれるバス停・駅のポイントデータと、OD Cost Matrixで作ったデータを使って、internal join（両方のデータが合致する行のみ残す）（バッファーポリゴンを使って切り出したデータは、必ずしも今回の分析対象となっていないため、実際に分析対象となったMake OD Cost Matrix Layerで残ったバス停・駅のリストを作成） 
* バス停・駅のリストのデータをArcGISからexcelファイルとしてexport 
* 各バス停のデータで1つのセルにまとまっている複数のバス路線のデータを、分解して、バス路線ごとに行を分ける → `BusRouteID`の列を作成して、路線ごとに番号を割り当てる
* 駅データについては、総武線は元データでは1つだが、総武快速線と緩行線はルートが違うので、停車駅である錦糸町のデータを快速線と緩行線で分ける → `RailwayID`の列を作成して、路線ごとに番号を割り当てる
* `TransitType`という列を鉄道・バスのデータの両方に作り、鉄道のデータにはTの列、バスにはBの列を付ける　 
* 対象となる鉄道・バス路線の時刻表の収集・運行頻度（平日の午前8時15分から午前9時15分の間）を入力（両方向に運行されている場合は、より頻繁に運行されている方向を採用）し、`BusStops.csv`と`Stations.csv`としてエクスポート（データ作成に使ったexcelファイルは`ServiceFrequencyCalc`というフォルダ内の`PTAL_TransitFq_Sumida.xlsx`）
    - 墨田区内の区間で真ん中付近にありかつ始発ではない駅を選択
    - 快速・普通などの運行区分がある場合には、路線全体で1つの運行頻度を適応しないように。快速停車駅かどうかの確認をして、各停しか止まらない駅のデータをそのまま快速停車駅に適応しないように。
    - 各路線の運行頻度の基準とした駅・バス停と基準とした方向をexcelに記録
    - 路線の一部だけ1方向のバス停がある。`NumberOfDirections`という列を作り、1方向運行（0）か、2方向運行（1）かを入力（PTALには含まれていないが、後々使う事があるかもしれないので念のため）

注：`MeshID`と`StationID`, `BusStopID`と同様にバス路線・鉄道路線についてもインデックスとは別で`BusRouteID`、`RailwayID`、というのを作っておく

#### Step 0-3: データの読み込み

In [1]:
import geopandas as gpd
import pandas as pd
import numpy as np
import folium
import branca.colormap as cm

#墨田区の100m四方のメッシュポリゴン(shp)の読み込み
mesh = gpd.read_file("data/Sumida_mesh.geojson")

#各メッシュの中心点と各SAP(service access points：徒歩640m圏内にあるバス停、徒歩960m圏内にある駅）を結んだshpの読み込み
mesh_busstop = gpd.read_file("data/mesh_to_busstops.geojson")
mesh_station = gpd.read_file("data/mesh_to_stations.geojson")

#各バス停における各バスルートの運行頻度データ(csv)の読み込み
busstop = pd.read_csv("data/BusStops.csv")
station = pd.read_csv("data/Stations.csv")

---

#### Step 1: 各SAPへの歩行時間の計算

In [2]:
#メッシュの中心点とSAPを結ぶデータには所要時間も入っている（'Total_Walk'）が、
#5km/hの歩行速度で計算されたものなので、
#距離データ（'Total_Kilo'）を使って、4.8km/hの歩行速度での所要時間に変換

mesh_busstop['WalkTime'] = mesh_busstop['Total_Kilometers']/4.8*60
mesh_station['WalkTime'] = mesh_station['Total_Kilometers']/4.8*60

#### Step 2: 各SAPの予定待ち時間（SWT）の算出

In [3]:
#SWT(scheduled waiting time) = 0.5 * (60/頻度)
busstop['SWT'] = 0.5*(60/ busstop['PeakHourFq'])
station['SWT'] = 0.5*(60/ station['PeakHourFq'])

#### Step 3: 各SAPの平均待ち時間（AWT）の算出

In [4]:
#AWT(average waiting times)=SWT + 信頼係数
#バスには信頼性係数2分、鉄道、地下鉄、路面電車には信頼性係数0.75分
busstop['AWT'] = busstop['SWT']+2
station['AWT'] = station['SWT']+0.75

#### Step 4: 各SAPの各ルートの合計アクセス時間（TAT）の算出

In [5]:
#joinをする（many to many）：左にgdf、右にcsv、BusStopIDとStationIDをキーに
joined_mesh_busstop = pd.merge(mesh_busstop, busstop, on='BusStopID', how='left', suffixes=('', '_from_busstop'))
joined_mesh_station = pd.merge(mesh_station, station, on='StationID', how='left', suffixes=('', '_from_station'))

1つのメッシュに紐づけられているアクセスポイントのうち、1つのルートが複数の停留所・駅を有する場合、最寄りの停留所のみが考慮される。なので、以下で、最寄りの停留所以外はTATがNaNになるように処理。

In [6]:
#まずはバスについて
#MeshIDとTrainRouteIDが共通する行ごとグループ化し、各グループ内でWalkTimeが最小の行のindexを抽出
#（つまり、min_indices_busというseriesデータには最小でない行のindex情報は含まれない）
min_indices_bus = joined_mesh_busstop.groupby(['MeshID', 'BusRouteID'])['WalkTime'].idxmin()

#'ClosestInRoute' 列を作成し、初期化して用意（すべてNaN）
joined_mesh_busstop['ClosestInRoute'] = np.nan

#min_indices_busというseriesデータにindexが含まれている行だけ1に設定
joined_mesh_busstop.loc[min_indices_bus, 'ClosestInRoute'] = 1

In [7]:
#次に鉄道について
#MeshIDとBusRouteIDが共通する行ごとグループ化し、各グループ内でWalkTimeが最小の行のindexを抽出
#（つまり、min_indices_trainというseriesデータには最小でない行のindex情報は含まれない）
min_indices_train = joined_mesh_station.groupby(['MeshID', 'RailwayID'])['WalkTime'].idxmin()

#'ClosestInRoute' 列を作成し、初期化して用意（すべてNaN）
joined_mesh_station['ClosestInRoute'] = np.nan

#min_indices_trainというseriesデータにindexが含まれている行だけ1に設定
joined_mesh_station.loc[min_indices_train, 'ClosestInRoute'] = 1

In [8]:
#TAT(total access time) = 移動時間（'WalkTime'）+AWT
#'ClosestInRoute'の行の値True/NaNをかけ合わせることで、同じMeshID内に含まれるBusRouteIDは最も近い停留所・駅のみに絞られる
joined_mesh_busstop['TAT']=(joined_mesh_busstop['WalkTime']+joined_mesh_busstop['AWT'])*joined_mesh_busstop['ClosestInRoute']
joined_mesh_station['TAT']=(joined_mesh_station['WalkTime']+joined_mesh_station['AWT'])*joined_mesh_station['ClosestInRoute']

#### Step5: 各SAPのEDFの算出

In [9]:
#EDF(equivalent doorstep frequency) = 0.5 * (60 / TAT)
#EDFはTATを時間ではなく頻度の単位に変換したもの
joined_mesh_busstop['EDF']=0.5*(60/joined_mesh_busstop['TAT'])
joined_mesh_station['EDF']=0.5*(60/joined_mesh_station['TAT'])

#### Step6: アクセス指数（AI）の算出

AI（Access Index）とは、各MeshIDについて、同じMeshIDをもつ行の中でEDFが最も高いものに1の重みを与え、同じMeshIDをもつ行の中で他のすべてのEDFには0.5の重みを与える。その上で、各MeshIDごとにそれらを合計（sum）したものである。  
各MeshのAI = 各Mesh最大のEDF + 0.5 * ∑(同じMeshIDをもつその他のすべてのEDF)

#### バスのAIを計算

In [10]:
# すべての行に weight 列を追加（初期は 0.5）
joined_mesh_busstop['weight'] = 0.5

# 各 MeshID ごとに EDF が最大の行の index を特定
max_indices_bus = joined_mesh_busstop.groupby('MeshID')['EDF'].idxmax()
max_indices_bus = max_indices_bus.dropna().astype(int)  #NaNを除去し、整数型に変換

# その行だけ weight を 1 にする
joined_mesh_busstop.loc[max_indices_bus, 'weight'] = 1.0

# weightを掛けたEDFを算出
joined_mesh_busstop['weighted_EDF'] = joined_mesh_busstop['EDF'] * joined_mesh_busstop['weight']

# AI を計算
AI_bus = joined_mesh_busstop.groupby('MeshID')['weighted_EDF'].sum().reset_index(name='AI')

##### 作成したデータの中身の確認

In [11]:
# 各セットを取得
ai_set = set(AI_bus['MeshID'])
mesh_set = set(mesh['MeshID'])

# AIにはあるがmeshにはないMeshID
only_in_ai = ai_set - mesh_set

# meshにはあるがAIにはないMeshID
only_in_mesh = mesh_set - ai_set

print("AIにしかないMeshID:", only_in_ai)
print("meshにしかないMeshID:", only_in_mesh)

AIにしかないMeshID: set()
meshにしかないMeshID: {1152, 1408, 1409, 1400, 1287, 1288, 1415, 1416, 1417, 1421, 1422, 1423, 1427, 1428, 1429, 1435, 1436, 1439, 1440, 1442, 1443, 1444, 1407, 1089, 1098, 1099, 1363, 1108, 1109, 1364, 1117, 1118, 1119, 1373, 1374, 1381, 1126, 1127, 1128, 1129, 1382, 1383, 1390, 1391, 1392, 1139, 1143, 1144, 1401, 1147, 1148, 1399, 1150, 1151}


この差の54個のmeshIDはすべて北東部の川沿いであることが判明。  
MeshIDは以下のすべて。これらの行についてはAIが出てこないことに留意。  
1089, 1098, 1099, 1108, 1109, 1117, 1118, 1119, 1126, 1127, 1128, 1129, 1139, 1143, 1144, 1147, 1148, 1150, 1151, 1152, 1287, 1288, 1363, 1364, 1373, 1374, 1381, 1382, 1383, 1390, 1391, 1392, 1399, 1400, 1401, 1407, 1408, 1409, 1415, 1416, 1417, 1421, 1422, 1423, 1427, 1428, 1429, 1435, 1436, 1439, 1440, 1442, 1443, 1444  

In [12]:
AI_bus['AI'].isnull().sum()

0

busstopという運行頻度データにはデータが入っているが、null valueの路線も存在する
そのためMeshIDによっては、運行の無いバス路線としか紐づいていないものも存在するかと懸念したが、それは無かった

#### 鉄道のAIを計算

In [13]:
# すべての行に weight 列を追加（初期は 0.5）
joined_mesh_station['weight'] = 0.5

# 各 MeshID ごとに EDF が最大の行の index を特定
max_indices_train = joined_mesh_station.groupby('MeshID')['EDF'].idxmax()
max_indices_train = max_indices_train.dropna().astype(int)  #NaNを除去し、整数型に変換

# その行だけ weight を 1 にする
joined_mesh_station.loc[max_indices_train, 'weight'] = 1.0

# weightを掛けたEDFを算出
joined_mesh_station['weighted_EDF'] = joined_mesh_station['EDF'] * joined_mesh_station['weight']

# AI を計算
AI_train = joined_mesh_station.groupby('MeshID')['weighted_EDF'].sum().reset_index(name='AI')

##### 作成したデータの中身の確認

In [14]:
# 各セットを取得
ai_set = set(AI_train['MeshID'])
mesh_set = set(mesh['MeshID'])

# AIにはあるがeshにはないMeshID
only_in_ai = ai_set - mesh_set

# meshにはあるがAIにはないMeshID
only_in_mesh = mesh_set - ai_set

print("AIにしかないMeshID:", only_in_ai)
print("meshにしかないMeshID:", only_in_mesh)

AIにしかないMeshID: set()
meshにしかないMeshID: {1036, 1037, 1038, 1039, 1044, 1045, 1046, 1047, 1048, 1049, 1053, 1054, 1055, 1056, 1057, 1058, 1059, 1062, 1063, 1064, 1065, 1066, 1067, 1068, 1069, 1076, 1077, 1078, 1079, 1087, 1088, 1089, 1097, 1098, 1099, 1108, 1109, 1117, 1118, 1119, 1128, 1129, 1130, 1131, 1132, 1133, 1134, 1135, 1136, 1137, 1138, 1139, 1140, 1141, 1142, 1143, 1144, 1145, 1146, 1147, 1148, 1149, 1150, 1151, 1152, 1154, 1155, 1157, 1158, 1160, 1161, 1163, 1164, 1165, 1166, 1167, 1168, 1169, 1170, 1171, 1172, 1173, 1174, 1175, 1176, 1177, 1178, 1250, 262, 263, 1288, 1343, 1344, 1354, 1363, 1364, 861, 1373, 1374, 1382, 1383, 875, 1392, 881, 882, 373, 374, 375, 376, 1401, 892, 893, 894, 382, 385, 386, 898, 899, 903, 396, 397, 912, 916, 1430, 407, 920, 1433, 923, 1435, 1436, 926, 1438, 929, 493}


この差の134個のmeshIDは北西部・北部・東部の川沿いと南部の中央部であることが判明。  
MeshIDは以下のすべて。これらの行についてはAIが出てこないことに留意。  
262, 263, 373, 374, 375, 376, 382, 385, 386, 396, 397, 407, 493, 861, 875, 881, 882, 892, 893, 894, 898, 899, 903, 912, 916, 920, 923, 926, 929, 1036, 1037, 1038, 1039, 1044, 1045, 1046, 1047, 1048, 1049, 1053, 1054, 1055, 1056, 1057, 1058, 1059, 1062, 1063, 1064, 1065, 1066, 1067, 1068, 1069, 1076, 1077, 1078, 1079, 1087, 1088, 1089, 1097, 1098, 1099, 1108, 1109, 1117, 1118, 1119, 1128, 1129, 1130, 1131, 1132, 1133, 1134, 1135, 1136, 1137, 1138, 1139, 1140, 1141, 1142, 1143, 1144, 1145, 1146, 1147, 1148, 1149, 1150, 1151, 1152, 1154, 1155, 1157, 1158, 1160, 1161, 1163, 1164, 1165, 1166, 1167, 1168, 1169, 1170, 1171, 1172, 1173, 1174, 1175, 1176, 1177, 1178, 1250, 1288, 1343, 1344, 1354, 1363, 1364, 1373, 1374, 1382, 1383, 1392, 1401, 1430, 1433, 1435, 1436, 1438

#### メッシュのポリゴンデータとバス・鉄道それぞれのAIの値を結合

In [15]:
#AccessIndexという列はAI_busにもAI_trainにもあるので、重複しないようにAccessIndex_bus、AccessIndex_trainと列名を変える
AI_bus = AI_bus.rename(columns={'AI': 'AI_bus'})
AI_train = AI_train.rename(columns={'AI': 'AI_train'})

#meshとAI_bus、AI_trainにはそれぞれMeshIDという列が存在する
#その列をキーにして、eshのgeodataframeにAI_busとAI_trainのdataframeを結合
#まずmeshにAI_busを左結合
mesh_merged = mesh.merge(AI_bus, on='MeshID', how='left')
#さらにAI_trainを左結合
mesh_merged = mesh_merged.merge(AI_train, on='MeshID', how='left')

In [16]:
#esh_mergedというgeodataframeのAI_busとAI_trainの列の値について、null valueのものは0に置き換える
mesh_merged['AI_bus'] = mesh_merged['AI_bus'].fillna(0)
mesh_merged['AI_train'] = mesh_merged['AI_train'].fillna(0)

In [17]:
#最終的なAccessIndexを算出
mesh_merged['AI']=mesh_merged['AI_bus']+mesh_merged['AI_train']

#### 総合のAIをマッピング

In [18]:
mesh_merged = mesh_merged.to_crs(epsg=4326)

# 地図の中心を計算
centroid = mesh_merged.geometry.centroid
center_lat = centroid.y.mean()
center_lon = centroid.x.mean()

# Foliumマップの作成
m = folium.Map(location=[center_lat, center_lon], zoom_start=13, tiles='CartoDB positron')

# AI列の最大最小
min_val = mesh_merged['AI'].min()
max_val = mesh_merged['AI'].max()

# カラーマップを定義（カラースキーム定義と反転）
original_colormap = cm.linear.Spectral_11
reversed_colors = list(original_colormap.colors)[::-1]  # 色を逆順に
colormap = cm.LinearColormap(reversed_colors, vmin=min_val, vmax=max_val)
colormap.caption = 'Access Index (AI)'

# GeoJsonでマップに描画
folium.GeoJson(
    mesh_merged,
    name="AI Layer",
    style_function=lambda feature: {
        'fillColor': colormap(feature['properties']['AI']),
        'color': 'None', #境界線は無しで設定
        'weight': 0,
        'fillOpacity': 0.7
    },
    tooltip=folium.GeoJsonTooltip(fields=['MeshID', 'AI'])
).add_to(m)

# カラーマップをマップに追加
colormap.add_to(m)

m.save("AI.html")
m

/var/folders/lx/_3z8wwyx3ds15_0k28hby_h80000gn/T/ipykernel_16856/2542504166.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = mesh_merged.geometry.centroid


#### 鉄道のAIをマッピング

In [19]:
# 地図の中心座標を計算
centroid = mesh_merged.geometry.centroid
center_lat = centroid.y.mean()
center_lon = centroid.x.mean()

# Foliumマップの作成
m = folium.Map(location=[center_lat, center_lon], zoom_start=13, tiles='CartoDB positron')

# 値の範囲を取得
min_val = mesh_merged['AI_train'].min()
max_val = mesh_merged['AI_train'].max()

# カラーマップを定義（カラースキーム定義と反転）
original_colormap = cm.linear.Spectral_11
reversed_colors = list(original_colormap.colors)[::-1]  # 色を逆順に
colormap = cm.LinearColormap(reversed_colors, vmin=min_val, vmax=max_val)
colormap.caption = 'Access Index (Train)'

# GeoJsonで可視化
folium.GeoJson(
    mesh_merged,
    name="AI_train Layer",
    style_function=lambda feature: {
        'fillColor': colormap(feature['properties']['AI_train']),
        'color': 'None', #境界線は無しで設定
        'weight': 0,
        'fillOpacity': 0.7,
    },
    tooltip=folium.GeoJsonTooltip(fields=['MeshID', 'AI_train'])
).add_to(m)

# カラーマップを追加
colormap.add_to(m)

m.save("AI_train.html")
m

/var/folders/lx/_3z8wwyx3ds15_0k28hby_h80000gn/T/ipykernel_16856/3136413731.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = mesh_merged.geometry.centroid


#### バスのAIをマッピング

In [20]:
# 地図の中心座標を計算
centroid = mesh_merged.geometry.centroid
center_lat = centroid.y.mean()
center_lon = centroid.x.mean()

# Foliumマップの作成
m = folium.Map(location=[center_lat, center_lon], zoom_start=13, tiles='CartoDB positron')

# 値の範囲を取得
min_val = mesh_merged['AI_bus'].min()
max_val = mesh_merged['AI_bus'].max()

# カラーマップを定義（カラースキーム定義と反転）
original_colormap = cm.linear.Spectral_11
reversed_colors = list(original_colormap.colors)[::-1]  # 色を逆順に
colormap = cm.LinearColormap(reversed_colors, vmin=min_val, vmax=max_val)
colormap.caption = 'Access Index (Bus)'

# GeoJsonで可視化
folium.GeoJson(
    mesh_merged,
    name="AI_bus Layer",
    style_function=lambda feature: {
        'fillColor': colormap(feature['properties']['AI_bus']),
        'color': 'None', #境界線は無しで設定
        'weight': 0,
        'fillOpacity': 0.7,
    },
    tooltip=folium.GeoJsonTooltip(fields=['MeshID', 'AI_bus'])
).add_to(m)

# カラーマップを追加
colormap.add_to(m)

m.save("AI_bus.html")
m

/var/folders/lx/_3z8wwyx3ds15_0k28hby_h80000gn/T/ipykernel_16856/322114141.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = mesh_merged.geometry.centroid


#### Step 7: AIをPTALへ変換

In [21]:
# 区切りの境界値（bin）を定義
bins = [-0.01, 0, 2.5, 5, 10, 15, 20, 25, 40, float('inf')]

# PTAL スコアラベルを設定
labels = ['0 (worst)', '1a', '1b', '2', '3', '4', '5', '6a', '6b (best)']

# PTALの値を格納する列を作成
mesh_merged['PTAL'] = pd.cut(mesh_merged['AI'], bins=bins, labels=labels)

#### PTALのMapping

In [22]:
# 1. PTALスコア分類
bins = [-0.01, 0, 2.5, 5, 10, 15, 20, 25, 40, float('inf')]
labels = ['0 (worst)', '1a', '1b', '2', '3', '4', '5', '6a', '6b (best)']
mesh_merged['PTAL'] = pd.cut(mesh_merged['AI'], bins=bins, labels=labels)

# 2. 色スキーム定義
ptal_colors = {
    '0 (worst)': '#FFFFFF',
    '1a': '#1F3B73',
    '1b': '#2F69BF',
    '2': '#57A0D3',
    '3': '#A5C76F',
    '4': '#FFF24D',
    '5': '#F9C791',
    '6a': '#E23228',
    '6b (best)': '#6B0000'
}

# 3. 地図作成
center = mesh_merged.geometry.centroid.unary_union.centroid
m = folium.Map(location=[center.y, center.x], zoom_start=13, tiles='CartoDB positron')

# 4. GeoJson レイヤー追加
folium.GeoJson(
    mesh_merged,
    name="PTAL Map",
    style_function=lambda feature: {
        'fillColor': ptal_colors.get(feature['properties']['PTAL'], '#808080'),
        'color': 'None', #境界線は無しで設定
        'weight': 0,
        'fillOpacity': 0.7
    },
    tooltip=folium.GeoJsonTooltip(fields=['MeshID', 'AI', 'PTAL'])
).add_to(m)

# 5. 凡例追加
legend_html = """
<div style="position: fixed; bottom: 20px; left: 20px; width: 160px; 
     background-color: white; z-index:9999; font-size:12px; 
     border:1px solid grey; padding: 8px;">
<b>PTAL Score</b><br>
""" + "".join([
    f'<i style="background:{ptal_colors[label]};width:14px;height:10px;display:inline-block;margin-right:6px;border:1px solid black;"></i>{label}<br>'
    for label in labels
]) + "</div>"

m.get_root().html.add_child(folium.Element(legend_html))

m.save("PTAL.html")
m

/var/folders/lx/_3z8wwyx3ds15_0k28hby_h80000gn/T/ipykernel_16856/126078013.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center = mesh_merged.geometry.centroid.unary_union.centroid
/var/folders/lx/_3z8wwyx3ds15_0k28hby_h80000gn/T/ipykernel_16856/126078013.py:20: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  center = mesh_merged.geometry.centroid.unary_union.centroid


#### 作成したデータの保存

In [23]:
joined_mesh_busstop.to_file("created_data/joined_mesh_busstop.gpkg", driver="GPKG")
joined_mesh_station.to_file("created_data/joined_mesh_station.gpkg", driver="GPKG")
mesh_merged.to_file("created_data/mesh_merged.gpkg", driver="GPKG")

#### 留意点
- 運行種別
    - 新宿線や伊勢崎線、浅草線には快速と普通など運行種類の違いがある。同じ方向でも異なる行き先の場合もある。
    - ただ快速停車駅と普通のみ停車駅とでは運行頻度が違うので、路線で一律に運行頻度を適応せず、駅の種別で異なる時刻表を適用
    - 行き先の違いについては考慮しない。
    - 錦糸町駅は総武快速線と総武各駅停車線が両方停まる唯一の駅。それらを別のルートとして処理するかどうか。
        - 国土数値情報では別の路線としては処理されておらず、総武線という1つとしての扱い。ただ実際にはルートが異なるので、厳密には別路線として処理する事とする。

- 運行の方向性
    - PTALのマニュアルでは1方向運行か2方向運行かは加味しない
    - 今回は、後々方向性を加味して分析したくなる可能性を考慮して、1方向運行は1、2方向運行は2として`NumberOfDirections`という列にデータを入れておく
    - 始発のバス停・駅は `NumberOfDirections` を1を割り当て
    - 錦11など、一部区間だけ1方向のバス停がある事例がある
        - 路線図・時刻表を確認の上で、1方向のバス停には`NumberOfDirections`を1を割り当て
    - 上記以外の双方向の出発があるバス停には2を割り当て
    - 押上駅は構造が複雑で、4路線が乗り入れている。各路線の起点駅になっており、路線別で分けるとすべて1方向運行だが、実際には直通運転しているので2方向運行の実態。今回は1方向運行の4路線という処理にする（最もアクセス性の高い路線だけに1を掛ける、という重み付けの時に、路線を統合した場合と別々に処理した場合とで差が出るかもしれない）

- PTALでは、近いバス停は統合しているが鉄道駅についての言及はない
    - なので、鉄道駅についてまとめる必要はないが、今回は、国土数値情報が出している300m以内かつ同名の駅を対象としたグループ分けがあるので、そのデータは`StationIDGrouped`という列として残しておく

#### ロンドンのPTALの枠組みを墨田で適応する上で考慮しなければならない要素
- **歩行速度**（高齢者、東京）：
    - アクセスポイントまでの設定距離を短くするならば、Step1において`mesh_to_busstops.geojson`と`mesh_to_stations.geojson`の`Total_Kilometers`や、計算に使う歩行速度を変更すればよい
    - アクセスポイントまでの設定距離を長くするならばArcGisProでのMake OD Cost Matrix Layerの操作設定を変更してデータを作り直す必要がある
- **遅延（信頼性係数）**（東京）：
    - Step3における係数を調整
- **採用する時間帯**
    - ラッシュアワーの時間帯（東京）
    - 高齢者の移動時間帯がラッシュアワーかどうか）（高齢者）
        - いずれもStep0-2（各SAPにおける運行頻度データの作成）においてデータを作り直す必要がある
- **バスと鉄道の重要性の比率**（東京）